In [51]:
%matplotlib inline

Generation of Questions with a seq2seq network 
*************************************************************

[KEY: > input, = target, < output]

   

This is made possible by the simple but powerful idea of the `sequence
to sequence network <http://arxiv.org/abs/1409.3215>`__, in which two
recurrent neural networks work together to transform one sequence to
another. An encoder network condenses an input sequence into a vector,
and a decoder network unfolds that vector into a new sequence.



To improve upon this model we'll use an `attention
mechanism <https://arxiv.org/abs/1409.0473>`__, which lets the decoder
learn to focus over a specific range of the input sequence.



In [52]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

Loading data files
===================

The data for this project is a set of many thousands of sentence pairs, broken down into two main groups i.e agreement and no agreement and are present in the dataset folder of the project



Similar to the character encoding used in the character-level RNN
tutorials, we will be representing each word in a language as a one-hot
vector, or giant vector of zeros except for a single one (at the index
of the word). 

We'll need a unique index per word to use as the inputs and targets of
the networks later. To keep track of all this we will use a helper class
called ``Lang`` which has word → index (``word2index``) and index → word
(``index2word``) dictionaries, as well as a count of each word
``word2count`` to use to later replace rare words.




In [53]:
SOS_token = 0
IDENT_TOKEN = -1
QUEST_TOKEN = -1
EOS_TOKEN =1
input_file_path = "./../data/no_agreement/"
agreement = False

class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

We shall convert all the words to lower case.

In [54]:
# Converts all to lowercase
def normalizeString(s):
    s = (s.lower().strip())
    return s

To read the data file we will split the file into lines, and then split
lines into pairs




In [55]:
def readLangs(lang1, lang2, reverse=False):
    print("Reading lines...")

    # Read the file and split into lines
    lines = open(input_file_path+'train.txt' ,).\
        read().strip().split('\n')

    # Split every line into pairs and normalize
    pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]

    # Reverse pairs, make Lang instances
    if reverse:
        pairs = [list(reversed(p)) for p in pairs]
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)

    return input_lang, output_lang, pairs

The maximum length of each sentence has been set to a 100 words.



In [56]:
MAX_LENGTH = 100
def filterPairs(pairs):
    return [pair for pair in pairs]

The full process for preparing the data is:

-  Read text file and split into lines, split lines into pairs
-  Normalize text, filter by length and content
-  Make word lists from sentences in pairs




In [57]:
def prepareData(lang1, lang2, reverse=False):
    input_lang, output_lang, pairs = readLangs(lang1, lang2, reverse)
    print("Read %s sentence pairs" % len(pairs))
    pairs = filterPairs(pairs)
    print("Trimmed to %s sentence pairs" % len(pairs))
    print("Counting words...")
    for pair in pairs:
        input_lang.addSentence(pair[0])
        output_lang.addSentence(pair[1])
    print("Counted words:")
    print(input_lang.name, input_lang.n_words)
    print(output_lang.name, output_lang.n_words)
    return input_lang, output_lang, pairs


input_lang, output_lang, pairs = prepareData('out', 'inp', True)
IDENT_TOKEN = input_lang.word2index["ident"]
QUEST_TOKEN = input_lang.word2index["quest"]
print(random.choice(pairs))

Reading lines...
Read 117878 sentence pairs
Trimmed to 117878 sentence pairs
Counting words...
Counted words:
inp 55
out 56
['our monkeys would impress the unicorn that can irritate the monkeys . ident', 'our monkeys would impress the unicorn that can irritate the monkeys . ident']


The Seq2Seq Model
=================

A Recurrent Neural Network, or RNN, is a network that operates on a
sequence and uses its own output as input for subsequent steps.

A `Sequence to Sequence network <http://arxiv.org/abs/1409.3215>`__, or
seq2seq network, or `Encoder Decoder
network <https://arxiv.org/pdf/1406.1078v3.pdf>`__, is a model
consisting of two RNNs called the encoder and decoder. The encoder reads
an input sequence and outputs a single vector, and the decoder reads
that vector to produce an output sequence.


Unlike sequence prediction with a single RNN, where every input
corresponds to an output, the seq2seq model frees us from sequence
length and order, which makes it ideal for translation between two
languages.

With a seq2seq model the encoder creates a single vector which, in the
ideal case, encodes the "meaning" of the input sequence into a single
vector — a single point in some N dimensional space of sentences.

The Encoder
-----------

The encoder of a seq2seq network is a RNN that outputs some value for
every word from the input sentence. For every input word the encoder
outputs a vector and a hidden state, and uses the hidden state for the
next input word.

In [58]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)

    def forward(self, input, hidden):
        embedded = self.embedding(input).view(1, 1, -1)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output, hidden

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)

The Decoder
-----------

The decoder is another RNN that takes the encoder output vector(s) and
outputs a sequence of words to create the translation.




Simple Decoder
-----------

In the simplest seq2seq decoder we use only last output of the encoder.
This last output is sometimes called the *context vector* as it encodes
context from the entire sequence. This context vector is used as the
initial hidden state of the decoder.

At every step of decoding, the decoder is given an input token and
hidden state. The initial input token is the start-of-string ``<SOS>``
token, and the first hidden state is the context vector (the encoder's
last hidden state).

In [59]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(output_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        output = self.embedding(input).view(1, 1, -1)
        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        output = self.softmax(self.out(output[0]))
        return output, hidden

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)

Attention Decoder
-----------


If only the context vector is passed betweeen the encoder and decoder,
that single vector carries the burden of encoding the entire sentence.

Attention allows the decoder network to "focus" on a different part of
the encoder's outputs for every step of the decoder's own outputs. First
we calculate a set of *attention weights*. These will be multiplied by
the encoder output vectors to create a weighted combination. The result
(called ``attn_applied`` in the code) should contain information about
that specific part of the input sequence, and thus help the decoder
choose the right output words.


Calculating the attention weights is done with another feed-forward
layer ``attn``, using the decoder's input and hidden state as inputs.
Because there are sentences of all sizes in the training data, to
actually create and train this layer we have to choose a maximum
sentence length (input length, for encoder outputs) that it can apply
to. Sentences of the maximum length will use all the attention weights,
while shorter sentences will only use the first few.

In [60]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, dropout_p=0.1, max_length=MAX_LENGTH):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length = max_length

        self.embedding = nn.Embedding(self.output_size, self.hidden_size)
        self.attn = nn.Linear(self.hidden_size * 2, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size * 2, self.hidden_size)
        self.dropout = nn.Dropout(self.dropout_p)
        self.gru = nn.GRU(self.hidden_size, self.hidden_size)
        self.out = nn.Linear(self.hidden_size, self.output_size)

    def forward(self, input, hidden, encoder_outputs):
        embedded = self.embedding(input).view(1, 1, -1)
        embedded = self.dropout(embedded)

        attn_weights = F.softmax(
            self.attn(torch.cat((embedded[0], hidden[0]), 1)), dim=1)
        attn_applied = torch.bmm(attn_weights.unsqueeze(0),
                                 encoder_outputs.unsqueeze(0))

        output = torch.cat((embedded[0], attn_applied[0]), 1)
        output = self.attn_combine(output).unsqueeze(0)

        output = F.relu(output)
        output, hidden = self.gru(output, hidden)

        output = F.log_softmax(self.out(output[0]), dim=1)
        return output, hidden, attn_weights

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)



Training
========

Preparing Training Data
-----------------------

To train, for each pair we will need an input tensor (indexes of the
words in the input sentence) and target tensor (indexes of the words in
the target sentence). While creating these vectors we will append the
EOS token to both sequences.




In [61]:
def indexesFromSentence(lang, sentence):
    return [lang.word2index[word] for word in sentence.split(' ')]


def tensorFromSentence(lang, sentence):
    indexes = indexesFromSentence(lang, sentence)
    if(indexes[-1]!=lang.word2index["ident"] and indexes[-1]!=lang.word2index["quest"]):
        indexes.append(EOS_TOKEN)
        
    return torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)


def tensorsFromPair(pair):
    input_tensor = tensorFromSentence(input_lang, pair[0])
    target_tensor = tensorFromSentence(output_lang, pair[1])
    return (input_tensor, target_tensor)

Training the Model
------------------

To train we run the input sentence through the encoder, and keep track
of every output and the latest hidden state. Then the decoder is given
the ``<SOS>`` token as its first input, and the last hidden state of the
encoder as its first hidden state.

"Teacher forcing" is the concept of using the real target outputs as
each next input, instead of using the decoder's guess as the next input.
Using teacher forcing causes it to converge faster but `when the trained
network is exploited, it may exhibit
instability <http://minds.jacobs-university.de/sites/default/files/uploads/papers/ESNTutorialRev.pdf>`__.

You can observe outputs of teacher-forced networks that read with
coherent grammar but wander far from the correct translation -
intuitively it has learned to represent the output grammar and can "pick
up" the meaning once the teacher tells it the first few words, but it
has not properly learned how to create the sentence from the translation
in the first place.

Because of the freedom PyTorch's autograd gives us, we can randomly
choose to use teacher forcing or not with a simple if statement. Turn
``teacher_forcing_ratio`` up to use more of it.




In [62]:
teacher_forcing_ratio = 0.5


def train(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, max_length=MAX_LENGTH):
    encoder_hidden = encoder.initHidden()

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0

    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(
            input_tensor[ei], encoder_hidden)
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden

    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    if use_teacher_forcing:
        # Teacher forcing: Feed the target as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]  # Teacher forcing

    else:
        # Without teacher forcing: use its own predictions as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == IDENT_TOKEN or decoder_input.item() == QUEST_TOKEN or decoder_input.item()== EOS_TOKEN:
                break

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

This is a helper function to print time elapsed and estimated time
remaining given the current time and progress %.




In [63]:
import time
import math


def asMinutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)


def timeSince(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (- %s)' % (asMinutes(s), asMinutes(rs))

The whole training process looks like this:

-  Start a timer
-  Initialize optimizers and criterion
-  Create set of training pairs
-  Start empty losses array for plotting

Then we call ``train`` many times and occasionally print the progress (%
of examples, time so far, estimated time) and average loss.




In [64]:
def trainIters(encoder, decoder, n_iters, print_every=1000, plot_every=100, learning_rate=0.01):
    start = time.time()
    plot_losses = []
    print_loss_total = 0  # Reset every print_every
    plot_loss_total = 0  # Reset every plot_every

    encoder_optimizer = optim.SGD(encoder.parameters(), lr=learning_rate)
    decoder_optimizer = optim.SGD(decoder.parameters(), lr=learning_rate)
    training_pairs = [tensorsFromPair(random.choice(pairs))
                      for i in range(n_iters)]
    criterion = nn.NLLLoss()

    for iter in range(1, n_iters + 1):
        training_pair = training_pairs[iter - 1]
        input_tensor = training_pair[0]
        target_tensor = training_pair[1]

        loss = train(input_tensor, target_tensor, encoder,
                     decoder, encoder_optimizer, decoder_optimizer, criterion)
        print_loss_total += loss
        plot_loss_total += loss

        if iter % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print('%s (%d %d%%) %.4f' % (timeSince(start, iter / n_iters),
                                         iter, iter / n_iters * 100, print_loss_avg))

        if iter % plot_every == 0:
            plot_loss_avg = plot_loss_total / plot_every
            plot_losses.append(plot_loss_avg)
            plot_loss_total = 0

    showPlot(plot_losses)

Plotting results
----------------

Plotting is done with matplotlib, using the array of loss values
``plot_losses`` saved while training.




In [65]:
import matplotlib.pyplot as plt
plt.switch_backend('agg')
import matplotlib.ticker as ticker
import numpy as np


def showPlot(points):
    plt.figure()
    fig, ax = plt.subplots()
    # this locator puts ticks at regular intervals
    loc = ticker.MultipleLocator(base=0.2)
    ax.yaxis.set_major_locator(loc)
    plt.plot(points)

Evaluation
==========

Evaluation is mostly the same as training, but there are no targets so
we simply feed the decoder's predictions back to itself for each step.
Every time it predicts a word we add it to the output string, and if it
predicts the EOS token we stop there. We also store the decoder's
attention outputs for display later.




In [66]:
def evaluate(encoder, decoder, sentence, max_length=MAX_LENGTH):
    with torch.no_grad():
        input_tensor = tensorFromSentence(input_lang, sentence)
        input_length = input_tensor.size()[0]
        encoder_hidden = encoder.initHidden()

        encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

        for ei in range(input_length):
            encoder_output, encoder_hidden = encoder(input_tensor[ei],
                                                     encoder_hidden)
            encoder_outputs[ei] += encoder_output[0, 0]

        decoder_input = torch.tensor([[SOS_token]], device=device)  # SOS

        decoder_hidden = encoder_hidden

        decoded_words = []
        decoder_attentions = torch.zeros(max_length, max_length)

        for di in range(max_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            decoder_attentions[di] = decoder_attention.data
            topv, topi = decoder_output.data.topk(1)
            if topi.item() == IDENT_TOKEN :
                decoded_words.append('<IDENT>')
                break
            elif topi.item() == QUEST_TOKEN :
                decoded_words.append('<QUEST>')
                break
            elif topi.item() == EOS_TOKEN :
                decoded_words.append('<EOS>')
                break
            else:
                decoded_words.append(output_lang.index2word[topi.item()])

            decoder_input = topi.squeeze().detach()

        return decoded_words, decoder_attentions[:di + 1]

We can evaluate random sentences from the training set and print out the
input, target, and output to make some subjective quality judgements:




In [67]:
def evaluateRandomly(encoder, decoder, n=10):
    for i in range(n):
        pair = random.choice(pairs)
        print('>', pair[0])
        print('=', pair[1])
        output_words, attentions = evaluate(encoder, decoder, pair[0])
        output_sentence = ' '.join(output_words)
        print('<', output_sentence)
        print('')

Training and Evaluating
=======================



In [68]:
class TheModelClass(nn.Module):
    def __init__(self):
        super(TheModelClass, self).__init__()
        self.conv1 = nn.Conv2d(3, 6, 5)
        self.pool = nn.MaxPool2d(2, 2)
        self.conv2 = nn.Conv2d(6, 16, 5)
        self.fc1 = nn.Linear(16 * 5 * 5, 120)
        self.fc2 = nn.Linear(120, 84)
        self.fc3 = nn.Linear(84, 10)

    def forward(self, x):
        x = self.pool(F.relu(self.conv1(x)))
        x = self.pool(F.relu(self.conv2(x)))
        x = x.view(-1, 16 * 5 * 5)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x

# Initialize model
model = TheModelClass()

# Initialize optimizer
optimizer = optim.SGD(model.parameters(), lr=0.001, momentum=0.9)

# Print model's state_dict
print("Model's state_dict:")
for param_tensor in model.state_dict():
    print(param_tensor, "\t", model.state_dict()[param_tensor].size())

# Print optimizer's state_dict
print("Optimizer's state_dict:")
for var_name in optimizer.state_dict():
    print(var_name, "\t", optimizer.state_dict()[var_name])


Model's state_dict:
conv1.weight 	 torch.Size([6, 3, 5, 5])
conv1.bias 	 torch.Size([6])
conv2.weight 	 torch.Size([16, 6, 5, 5])
conv2.bias 	 torch.Size([16])
fc1.weight 	 torch.Size([120, 400])
fc1.bias 	 torch.Size([120])
fc2.weight 	 torch.Size([84, 120])
fc2.bias 	 torch.Size([84])
fc3.weight 	 torch.Size([10, 84])
fc3.bias 	 torch.Size([10])
Optimizer's state_dict:
state 	 {}
param_groups 	 [{'nesterov': False, 'params': [140283637269128, 140283637269200, 140283637269488, 140283637269848, 140283637269776, 140283637269272, 140283637268984, 140283637269704, 140283637268840, 140283637268768], 'lr': 0.001, 'weight_decay': 0, 'momentum': 0.9, 'dampening': 0}]


In [ ]:
hidden_size = 256
counter = 3

name = "no_agreement_"+str(counter)+".pt"
print(name)

encoder1 = EncoderRNN(input_lang.n_words, hidden_size).to(device)
attn_decoder1 = AttnDecoderRNN(hidden_size, output_lang.n_words, dropout_p=0.1).to(device)
trainIters(encoder1, attn_decoder1, 75000, print_every=50)

torch.save(model.state_dict(),name)   
counter+=1
    
  

no_agreement_3.pt
0m 3s (- 89m 20s) (50 0%) 3.3885
0m 4s (- 61m 27s) (100 0%) 3.0174
0m 6s (- 52m 30s) (150 0%) 3.0148
0m 7s (- 48m 7s) (200 0%) 2.8598
0m 9s (- 45m 18s) (250 0%) 2.7876
0m 10s (- 43m 34s) (300 0%) 2.9054
0m 11s (- 42m 30s) (350 0%) 2.7587
0m 13s (- 41m 48s) (400 0%) 2.7402
0m 15s (- 41m 29s) (450 0%) 2.8166
0m 16s (- 41m 41s) (500 0%) 2.5617
0m 18s (- 41m 49s) (550 0%) 2.5681
0m 20s (- 42m 2s) (600 0%) 2.4850
0m 22s (- 42m 5s) (650 0%) 2.5139
0m 23s (- 42m 5s) (700 0%) 2.4656
0m 25s (- 42m 1s) (750 1%) 2.3070
0m 27s (- 42m 8s) (800 1%) 2.4584
0m 28s (- 42m 4s) (850 1%) 2.4165
0m 30s (- 42m 4s) (900 1%) 2.3876
0m 32s (- 42m 9s) (950 1%) 2.4818
0m 34s (- 42m 0s) (1000 1%) 2.2948
0m 35s (- 42m 13s) (1050 1%) 2.3096
0m 37s (- 42m 11s) (1100 1%) 2.3096
0m 39s (- 42m 7s) (1150 1%) 2.2112
0m 41s (- 42m 3s) (1200 1%) 2.4377
0m 42s (- 42m 2s) (1250 1%) 2.3902
0m 44s (- 42m 3s) (1300 1%) 2.2417
0m 46s (- 42m 3s) (1350 1%) 2.4408
0m 47s (- 41m 59s) (1400 1%) 2.2602
0m 49s (- 42m 

6m 48s (- 38m 0s) (11400 15%) 0.2437
6m 50s (- 37m 59s) (11450 15%) 0.2499
6m 52s (- 37m 57s) (11500 15%) 0.2968
6m 54s (- 37m 55s) (11550 15%) 0.2757
6m 56s (- 37m 53s) (11600 15%) 0.2739
6m 57s (- 37m 52s) (11650 15%) 0.2809
6m 59s (- 37m 50s) (11700 15%) 0.2612
7m 1s (- 37m 49s) (11750 15%) 0.2447
7m 3s (- 37m 47s) (11800 15%) 0.2471
7m 5s (- 37m 45s) (11850 15%) 0.2976
7m 6s (- 37m 43s) (11900 15%) 0.3106
7m 8s (- 37m 42s) (11950 15%) 0.3212
7m 10s (- 37m 41s) (12000 16%) 0.2959
7m 13s (- 37m 42s) (12050 16%) 0.2700
7m 15s (- 37m 41s) (12100 16%) 0.2943
7m 16s (- 37m 40s) (12150 16%) 0.2817
7m 18s (- 37m 38s) (12200 16%) 0.2501
7m 20s (- 37m 36s) (12250 16%) 0.2282
7m 22s (- 37m 34s) (12300 16%) 0.2183
7m 23s (- 37m 32s) (12350 16%) 0.2917
7m 25s (- 37m 30s) (12400 16%) 0.2441
7m 27s (- 37m 29s) (12450 16%) 0.2173
7m 29s (- 37m 28s) (12500 16%) 0.2833
7m 31s (- 37m 26s) (12550 16%) 0.2340
7m 33s (- 37m 24s) (12600 16%) 0.2832
7m 35s (- 37m 23s) (12650 16%) 0.2610
7m 36s (- 37m 21s)

13m 26s (- 32m 4s) (22150 29%) 0.1203
13m 28s (- 32m 2s) (22200 29%) 0.1246
13m 30s (- 32m 0s) (22250 29%) 0.0565
13m 32s (- 31m 59s) (22300 29%) 0.1398
13m 33s (- 31m 57s) (22350 29%) 0.1079
13m 35s (- 31m 55s) (22400 29%) 0.0717
13m 37s (- 31m 53s) (22450 29%) 0.1112
13m 39s (- 31m 51s) (22500 30%) 0.0947
13m 41s (- 31m 49s) (22550 30%) 0.1110
13m 42s (- 31m 47s) (22600 30%) 0.1212
13m 44s (- 31m 46s) (22650 30%) 0.1165
13m 46s (- 31m 44s) (22700 30%) 0.1331
13m 48s (- 31m 42s) (22750 30%) 0.1005
13m 50s (- 31m 41s) (22800 30%) 0.0855
13m 52s (- 31m 39s) (22850 30%) 0.1415
13m 54s (- 31m 37s) (22900 30%) 0.1005
13m 55s (- 31m 35s) (22950 30%) 0.1022
13m 57s (- 31m 33s) (23000 30%) 0.0806
13m 59s (- 31m 31s) (23050 30%) 0.1279
14m 1s (- 31m 30s) (23100 30%) 0.1056
14m 3s (- 31m 28s) (23150 30%) 0.0898
14m 4s (- 31m 26s) (23200 30%) 0.1023
14m 6s (- 31m 24s) (23250 31%) 0.0778
14m 8s (- 31m 22s) (23300 31%) 0.0513
14m 10s (- 31m 21s) (23350 31%) 0.0900
14m 12s (- 31m 19s) (23400 31%) 0

20m 0s (- 25m 49s) (32750 43%) 0.0861
20m 2s (- 25m 47s) (32800 43%) 0.1874
20m 4s (- 25m 45s) (32850 43%) 0.0746
20m 6s (- 25m 43s) (32900 43%) 0.1618
20m 8s (- 25m 41s) (32950 43%) 0.0729
20m 9s (- 25m 39s) (33000 44%) 0.0627
20m 11s (- 25m 37s) (33050 44%) 0.0748
20m 13s (- 25m 36s) (33100 44%) 0.0915
20m 15s (- 25m 34s) (33150 44%) 0.0740
20m 17s (- 25m 32s) (33200 44%) 0.0587
20m 19s (- 25m 30s) (33250 44%) 0.0989
20m 21s (- 25m 29s) (33300 44%) 0.0695
20m 23s (- 25m 27s) (33350 44%) 0.0553
20m 24s (- 25m 25s) (33400 44%) 0.0540
20m 26s (- 25m 23s) (33450 44%) 0.0806
20m 28s (- 25m 21s) (33500 44%) 0.0461
20m 30s (- 25m 19s) (33550 44%) 0.0618
20m 31s (- 25m 17s) (33600 44%) 0.1037
20m 33s (- 25m 16s) (33650 44%) 0.0873
20m 35s (- 25m 14s) (33700 44%) 0.0690
20m 37s (- 25m 12s) (33750 45%) 0.0519
20m 39s (- 25m 10s) (33800 45%) 0.0614
20m 41s (- 25m 8s) (33850 45%) 0.0714
20m 43s (- 25m 7s) (33900 45%) 0.0720
20m 45s (- 25m 5s) (33950 45%) 0.0522
20m 46s (- 25m 3s) (34000 45%) 0.0

26m 35s (- 19m 24s) (43350 57%) 0.0388
26m 36s (- 19m 22s) (43400 57%) 0.0360
26m 38s (- 19m 20s) (43450 57%) 0.0391
26m 40s (- 19m 19s) (43500 57%) 0.0390
26m 42s (- 19m 17s) (43550 58%) 0.0494
26m 44s (- 19m 15s) (43600 58%) 0.0262
26m 46s (- 19m 13s) (43650 58%) 0.0404
26m 47s (- 19m 11s) (43700 58%) 0.0279
26m 49s (- 19m 9s) (43750 58%) 0.0425
26m 51s (- 19m 8s) (43800 58%) 0.0456
26m 53s (- 19m 6s) (43850 58%) 0.0414
26m 55s (- 19m 4s) (43900 58%) 0.0359
26m 57s (- 19m 2s) (43950 58%) 0.0349
26m 59s (- 19m 0s) (44000 58%) 0.0426
27m 0s (- 18m 58s) (44050 58%) 0.0442
27m 2s (- 18m 57s) (44100 58%) 0.0390
27m 4s (- 18m 55s) (44150 58%) 0.0334
27m 6s (- 18m 53s) (44200 58%) 0.0507
27m 7s (- 18m 51s) (44250 59%) 0.0200
27m 9s (- 18m 49s) (44300 59%) 0.0240
27m 12s (- 18m 48s) (44350 59%) 0.0345
27m 14s (- 18m 46s) (44400 59%) 0.0240
27m 16s (- 18m 44s) (44450 59%) 0.0478
27m 18s (- 18m 42s) (44500 59%) 0.0343
27m 19s (- 18m 40s) (44550 59%) 0.0431
27m 21s (- 18m 39s) (44600 59%) 0.042

In [34]:
evaluateRandomly(encoder1, attn_decoder1)

> our rabbit upon our yaks does sleep . ident
= our rabbit upon our yaks does sleep . ident
< our rabbit upon our yaks does sleep . <IDENT>

> our rabbit does entertain my elephants . ident
= our rabbit does entertain my elephants . ident
< our rabbit does entertain my elephants . <IDENT>

> my monkey behind my elephants doesnt irritate some seal with my seal . quest
= doesnt my monkey behind my elephants irritate some seal with my seal ? quest
< doesnt my monkey behind my elephants irritate some seal with my seal <QUEST>

> your rabbit below your seals doesnt confuse your cats below our seals . ident
= your rabbit below your seals doesnt confuse your cats below our seals . ident
< your rabbit below your seals doesnt confuse your cats below our seals . <IDENT>

> our unicorns upon our cat dont sleep . ident
= our unicorns upon our cat dont sleep . ident
< our unicorns upon our cat dont sleep . <IDENT>

> your elephant does impress your elephants that do giggle . quest
= does your eleph

Visualizing Attention
---------------------

A useful property of the attention mechanism is its highly interpretable
outputs. Because it is used to weight specific encoder outputs of the
input sequence, we can imagine looking where the network is focused most
at each time step.

You could simply run ``plt.matshow(attentions)`` to see attention output
displayed as a matrix, with the columns being input steps and rows being
output steps:




In [71]:
output_words, attentions = evaluate(
    encoder1, attn_decoder1, "our cats do read quest")
plt.matshow(attentions.numpy())

KeyError: 'do'

For a better viewing experience we will do the extra work of adding axes
and labels:




In [36]:
def showAttention(input_sentence, output_words, attentions):
    # Set up figure with colorbar
    fig = plt.figure()
    ax = fig.add_subplot(111)
    cax = ax.matshow(attentions.numpy(), cmap='bone')
    fig.colorbar(cax)

    # Set up axes
    ax.set_xticklabels([''] + input_sentence.split(' ') +
                       ['<end>'], rotation=90)
    ax.set_yticklabels([''] + output_words)

    # Show label at every tick
    ax.xaxis.set_major_locator(ticker.MultipleLocator(1))
    ax.yaxis.set_major_locator(ticker.MultipleLocator(1))

    plt.show()
    fig.savefig(input_sentence+'.png')


def evaluateAndShowAttention(input_sentence):
    output_words, attentions = evaluate(
        encoder1, attn_decoder1, input_sentence)
    print('input =', input_sentence)
    print('output =', ' '.join(output_words))
    showAttention(input_sentence, output_words, attentions)


evaluateAndShowAttention("her dog who does smile doesnt confuse your dog who does confuse your unicorn . quest")



input = her dog who does smile doesnt confuse your dog who does confuse your unicorn . quest
output = does her dog who doesnt smile doesnt confuse your dog who does confuse your unicorn <QUEST>


/home/badwolf/.virtualenvs/dl/lib/python3.5/site-packages/matplotlib/figure.py:445: UserWarning: Matplotlib is currently using agg, which is a non-GUI backend, so cannot show the figure.
  % get_backend())


In [75]:
lines = open(input_file_path+'test.txt' ,).\
    read().strip().split('\n')
input_sentences = [] 
output_sentences = []
predicted_sentences = []
failed_full_p = []
failed_full_e = []
failed_pos_p = []
failed_pos_e = []
full_sentence_word_match_counter = 0
full_sentence_pos_match_counter = 0
total_sentences_counter = 0
from eval import *
import string
exclude = set(string.punctuation)

for index in range(len(lines)):
    sentences = lines[index].split("\t")
    normalizedString = (sentences[0].lower()).split(" ")
    #     print(normalizedString)
    normalizedString = list(ch for ch in normalizedString if ch not in exclude)
    #     print(normalizedString)
    input_sent =" ".join(normalizedString)
    #     print(input_sent)
    normalizedString = (sentences[1].lower()).split(" ")
    #     print(normalizedString)
    normalizedString = list(ch for ch in normalizedString if ch not in exclude)
    #     print(normalizedString)
    output_sent =" ".join(normalizedString)
    input_sentences.append(input_sent)
    output_sentences.append(output_sent)
    outwords , out_attn = evaluate(encoder1,attn_decoder1,input_sent,MAX_LENGTH)
    predicted_sentence = " ".join(outwords)
    predicted_sentences.append(predicted_sentence)
    pred = list(ch for ch in outwords if ch not in exclude)
    print(pred)
    if(pred[-1] != "." and pred[-1] != "?"):
        final_pred = pred[:len(pred)-1]
    else:
        final_expected = pred[:len(pred)-1]
    expected = output_sent.split(" ")
    final_expected = expected[:len(expected)-1]
    print(expected)
    print(final_expected)
    print("index" , total_sentences_counter)
    print("Count : pos" , full_sentence_pos_match_counter )
    print ("Count : full" , full_sentence_word_match_counter)
    print(final_pred,final_expected)
    if full_sentence_word_match(final_pred,final_expected):
        full_sentence_word_match_counter+=1
    else:
        failed_full_p.append(final_pred)
        failed_full_e.append(final_expected)
    if full_sentence_pos_match(final_pred,final_expected,agreement):
        full_sentence_pos_match_counter+=1
    else:
        failed_pos_p.append(final_pred)
        failed_pos_e.append(final_expected)
    total_sentences_counter+=1

predictions = open(input_file_path+"predictions_" + str(counter-1) + ".txt","w")
for index in range(total_sentences_counter):
    predictions.write(str(index)+".\n")
    predictions.write("Input:"+input_sentences[index] + "\n")
    predictions.write("Expected Output:" + output_sentences[index]+"\n")
    predictions.write("Predicted:" + predicted_sentences[index] + "\n")
predictions.close()

report = open(input_file_path+"report_" + str(counter-1) + ".txt" , "w")
report.write("Total number Of sentences:" + str(total_sentences_counter) + "\n")
report.write("Total number of correct full sentences word match:" + str(full_sentence_word_match_counter) + "\n")
report.write("Total number of correct full sentences pos match:" + str(full_sentence_pos_match_counter) + "\n")
report.close()

failed = open(input_file_path+"failed_full_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_full_e)):
    predicted = " ".join(failed_full_p[index])
    expected = " ".join(failed_full_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()
failed = open(input_file_path+"failed_pos_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_pos_e)):
    predicted = " ".join(failed_pos_p[index])
    expected = " ".join(failed_pos_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()

['the', 'monkey', 'who', 'would', 'giggle', 'would', 'admire', 'the', 'birds', 'upon', 'your', 'monkeys', '<IDENT>']
['the', 'monkey', 'who', 'would', 'giggle', 'would', 'admire', 'the', 'monkeys', 'upon', 'your', 'birds', 'ident']
['the', 'monkey', 'who', 'would', 'giggle', 'would', 'admire', 'the', 'monkeys', 'upon', 'your', 'birds']
index 0
Count : pos 0
Count : full 0
['the', 'monkey', 'who', 'would', 'giggle', 'would', 'admire', 'the', 'birds', 'upon', 'your', 'monkeys'] ['the', 'monkey', 'who', 'would', 'giggle', 'would', 'admire', 'the', 'monkeys', 'upon', 'your', 'birds']
['some', 'cats', 'can', 'entertain', 'our', 'seal', 'near', 'some', 'elephant', '<IDENT>']
['some', 'cats', 'can', 'entertain', 'our', 'seal', 'near', 'some', 'elephant', 'ident']
['some', 'cats', 'can', 'entertain', 'our', 'seal', 'near', 'some', 'elephant']
index 1
Count : pos 1
Count : full 0
['some', 'cats', 'can', 'entertain', 'our', 'seal', 'near', 'some', 'elephant'] ['some', 'cats', 'can', 'entertain',

['some', 'rabbits', 'would', 'confuse', 'some', 'seal', 'who', 'would', 'call', 'some', 'birds', '<IDENT>']
['some', 'rabbits', 'would', 'confuse', 'some', 'seal', 'who', 'would', 'call', 'some', 'birds', 'ident']
['some', 'rabbits', 'would', 'confuse', 'some', 'seal', 'who', 'would', 'call', 'some', 'birds']
index 19
Count : pos 18
Count : full 16
['some', 'rabbits', 'would', 'confuse', 'some', 'seal', 'who', 'would', 'call', 'some', 'birds'] ['some', 'rabbits', 'would', 'confuse', 'some', 'seal', 'who', 'would', 'call', 'some', 'birds']
['your', 'dogs', 'behind', 'our', 'monkey', 'would', 'call', 'our', 'monkey', 'around', 'our', 'monkey', '<IDENT>']
['your', 'dogs', 'behind', 'our', 'monkey', 'would', 'call', 'our', 'monkey', 'around', 'our', 'rabbits', 'ident']
['your', 'dogs', 'behind', 'our', 'monkey', 'would', 'call', 'our', 'monkey', 'around', 'our', 'rabbits']
index 20
Count : pos 19
Count : full 17
['your', 'dogs', 'behind', 'our', 'monkey', 'would', 'call', 'our', 'monkey', 

['the', 'yaks', 'who', 'will', 'sleep', 'could', 'irritate', 'the', 'yaks', 'with', 'your', 'dogs', '<IDENT>']
['the', 'yaks', 'who', 'will', 'sleep', 'could', 'irritate', 'the', 'yaks', 'with', 'your', 'dogs', 'ident']
['the', 'yaks', 'who', 'will', 'sleep', 'could', 'irritate', 'the', 'yaks', 'with', 'your', 'dogs']
index 36
Count : pos 34
Count : full 29
['the', 'yaks', 'who', 'will', 'sleep', 'could', 'irritate', 'the', 'yaks', 'with', 'your', 'dogs'] ['the', 'yaks', 'who', 'will', 'sleep', 'could', 'irritate', 'the', 'yaks', 'with', 'your', 'dogs']
['our', 'seal', 'who', 'can', 'giggle', 'can', 'irritate', 'some', 'seal', 'below', 'our', 'seal', '<IDENT>']
['our', 'seal', 'who', 'can', 'giggle', 'can', 'irritate', 'some', 'seal', 'below', 'our', 'seal', 'ident']
['our', 'seal', 'who', 'can', 'giggle', 'can', 'irritate', 'some', 'seal', 'below', 'our', 'seal']
index 37
Count : pos 35
Count : full 30
['our', 'seal', 'who', 'can', 'giggle', 'can', 'irritate', 'some', 'seal', 'below',

['your', 'monkey', 'behind', 'the', 'dog', 'would', 'confuse', 'the', 'dog', '<IDENT>']
['your', 'monkey', 'behind', 'the', 'dog', 'would', 'confuse', 'the', 'dog', 'ident']
['your', 'monkey', 'behind', 'the', 'dog', 'would', 'confuse', 'the', 'dog']
index 56
Count : pos 51
Count : full 46
['your', 'monkey', 'behind', 'the', 'dog', 'would', 'confuse', 'the', 'dog'] ['your', 'monkey', 'behind', 'the', 'dog', 'would', 'confuse', 'the', 'dog']
['some', 'elephant', 'who', 'some', 'elephant', 'can', 'live', 'would', 'entertain', 'your', 'seals', '<IDENT>']
['some', 'elephant', 'who', 'some', 'elephant', 'can', 'live', 'would', 'entertain', 'your', 'seals', 'ident']
['some', 'elephant', 'who', 'some', 'elephant', 'can', 'live', 'would', 'entertain', 'your', 'seals']
index 57
Count : pos 52
Count : full 47
['some', 'elephant', 'who', 'some', 'elephant', 'can', 'live', 'would', 'entertain', 'your', 'seals'] ['some', 'elephant', 'who', 'some', 'elephant', 'can', 'live', 'would', 'entertain', 'y

['will', 'your', 'cats', 'near', 'your', 'cats', 'confuse', 'the', 'cats', 'who', 'will', 'confuse', 'your', 'cats', '<QUEST>']
['will', 'your', 'cats', 'near', 'your', 'cats', 'confuse', 'the', 'cats', 'who', 'will', 'confuse', 'your', 'cats', 'quest']
['will', 'your', 'cats', 'near', 'your', 'cats', 'confuse', 'the', 'cats', 'who', 'will', 'confuse', 'your', 'cats']
index 73
Count : pos 64
Count : full 57
['will', 'your', 'cats', 'near', 'your', 'cats', 'confuse', 'the', 'cats', 'who', 'will', 'confuse', 'your', 'cats'] ['will', 'your', 'cats', 'near', 'your', 'cats', 'confuse', 'the', 'cats', 'who', 'will', 'confuse', 'your', 'cats']
['your', 'elephant', 'near', 'my', 'elephants', 'would', 'read', '<IDENT>']
['your', 'elephant', 'near', 'my', 'elephants', 'would', 'read', 'ident']
['your', 'elephant', 'near', 'my', 'elephants', 'would', 'read']
index 74
Count : pos 65
Count : full 58
['your', 'elephant', 'near', 'my', 'elephants', 'would', 'read'] ['your', 'elephant', 'near', 'my', 

...

['her', 'yak', 'that', 'the', 'dogs', 'can', 'giggle', 'could', 'entertain', 'the', 'dogs', '<IDENT>']
['her', 'yak', 'that', 'the', 'dogs', 'can', 'giggle', 'could', 'entertain', 'the', 'dogs', 'ident']
['her', 'yak', 'that', 'the', 'dogs', 'can', 'giggle', 'could', 'entertain', 'the', 'dogs']
index 8743
Count : pos 8282
Count : full 7601
['her', 'yak', 'that', 'the', 'dogs', 'can', 'giggle', 'could', 'entertain', 'the', 'dogs'] ['her', 'yak', 'that', 'the', 'dogs', 'can', 'giggle', 'could', 'entertain', 'the', 'dogs']
['my', 'dog', 'that', 'the', 'birds', 'could', 'smile', 'could', 'admire', 'the', 'birds', '<IDENT>']
['my', 'dog', 'that', 'the', 'birds', 'could', 'smile', 'could', 'admire', 'the', 'birds', 'ident']
['my', 'dog', 'that', 'the', 'birds', 'could', 'smile', 'could', 'admire', 'the', 'birds']
index 8744
Count : pos 8283
Count : full 7602
['my', 'dog', 'that', 'the', 'birds', 'could', 'smile', 'could', 'admire', 'the', 'birds'] ['my', 'dog', 'that', 'the', 'birds', 'could

['can', 'her', 'monkeys', 'impress', 'her', 'monkeys', 'by', 'your', 'monkeys', '<QUEST>']
['can', 'her', 'monkeys', 'impress', 'her', 'monkeys', 'by', 'your', 'monkeys', 'quest']
['can', 'her', 'monkeys', 'impress', 'her', 'monkeys', 'by', 'your', 'monkeys']
index 8760
Count : pos 8298
Count : full 7617
['can', 'her', 'monkeys', 'impress', 'her', 'monkeys', 'by', 'your', 'monkeys'] ['can', 'her', 'monkeys', 'impress', 'her', 'monkeys', 'by', 'your', 'monkeys']
['our', 'bird', 'who', 'could', 'laugh', 'can', 'call', 'some', 'cat', 'that', 'could', 'entertain', 'some', 'birds', '<IDENT>']
['our', 'bird', 'who', 'could', 'laugh', 'can', 'call', 'some', 'cat', 'that', 'could', 'entertain', 'some', 'birds', 'ident']
['our', 'bird', 'who', 'could', 'laugh', 'can', 'call', 'some', 'cat', 'that', 'could', 'entertain', 'some', 'birds']
index 8761
Count : pos 8299
Count : full 7618
['our', 'bird', 'who', 'could', 'laugh', 'can', 'call', 'some', 'cat', 'that', 'could', 'entertain', 'some', 'bird

['can', 'my', 'yak', 'upon', 'your', 'monkey', 'giggle', '<QUEST>']
['can', 'my', 'yak', 'upon', 'your', 'monkey', 'giggle', 'quest']
['can', 'my', 'yak', 'upon', 'your', 'monkey', 'giggle']
index 8777
Count : pos 8314
Count : full 7631
['can', 'my', 'yak', 'upon', 'your', 'monkey', 'giggle'] ['can', 'my', 'yak', 'upon', 'your', 'monkey', 'giggle']
['can', 'some', 'unicorn', 'around', 'some', 'unicorn', 'sleep', '<QUEST>']
['can', 'some', 'unicorn', 'around', 'some', 'unicorn', 'sleep', 'quest']
['can', 'some', 'unicorn', 'around', 'some', 'unicorn', 'sleep']
index 8778
Count : pos 8315
Count : full 7632
['can', 'some', 'unicorn', 'around', 'some', 'unicorn', 'sleep'] ['can', 'some', 'unicorn', 'around', 'some', 'unicorn', 'sleep']
['her', 'seals', 'would', 'confuse', 'our', 'dogs', '<IDENT>']
['her', 'seals', 'would', 'confuse', 'our', 'dogs', 'ident']
['her', 'seals', 'would', 'confuse', 'our', 'dogs']
index 8779
Count : pos 8316
Count : full 7633
['her', 'seals', 'would', 'confuse',

['the', 'yaks', 'will', 'confuse', 'the', 'dog', 'who', 'can', 'confuse', 'my', 'rabbit', '<IDENT>']
['the', 'yaks', 'will', 'confuse', 'the', 'dog', 'who', 'can', 'confuse', 'my', 'rabbit', 'ident']
['the', 'yaks', 'will', 'confuse', 'the', 'dog', 'who', 'can', 'confuse', 'my', 'rabbit']
index 8808
Count : pos 8342
Count : full 7658
['the', 'yaks', 'will', 'confuse', 'the', 'dog', 'who', 'can', 'confuse', 'my', 'rabbit'] ['the', 'yaks', 'will', 'confuse', 'the', 'dog', 'who', 'can', 'confuse', 'my', 'rabbit']
['can', 'your', 'cat', 'call', 'your', 'seal', 'who', 'would', 'entertain', 'your', 'seals', '<QUEST>']
['can', 'your', 'cat', 'call', 'your', 'seal', 'who', 'would', 'entertain', 'your', 'seals', 'quest']
['can', 'your', 'cat', 'call', 'your', 'seal', 'who', 'would', 'entertain', 'your', 'seals']
index 8809
Count : pos 8343
Count : full 7659
['can', 'your', 'cat', 'call', 'your', 'seal', 'who', 'would', 'entertain', 'your', 'seals'] ['can', 'your', 'cat', 'call', 'your', 'seal',

['the', 'yaks', 'who', 'can', 'giggle', 'will', 'entertain', 'some', 'yak', '<IDENT>']
['the', 'yaks', 'who', 'can', 'giggle', 'will', 'entertain', 'some', 'yak', 'below', 'some', 'yaks', 'ident']
['the', 'yaks', 'who', 'can', 'giggle', 'will', 'entertain', 'some', 'yak', 'below', 'some', 'yaks']
index 8824
Count : pos 8357
Count : full 7672
['the', 'yaks', 'who', 'can', 'giggle', 'will', 'entertain', 'some', 'yak'] ['the', 'yaks', 'who', 'can', 'giggle', 'will', 'entertain', 'some', 'yak', 'below', 'some', 'yaks']
['my', 'seals', 'who', 'will', 'giggle', 'could', 'admire', 'my', 'seals', 'who', 'some', 'cats', 'will', 'smile', '<IDENT>']
['my', 'seals', 'who', 'will', 'giggle', 'could', 'admire', 'my', 'seals', 'who', 'some', 'cats', 'will', 'smile', 'ident']
['my', 'seals', 'who', 'will', 'giggle', 'could', 'admire', 'my', 'seals', 'who', 'some', 'cats', 'will', 'smile']
index 8825
Count : pos 8357
Count : full 7672
['my', 'seals', 'who', 'will', 'giggle', 'could', 'admire', 'my', 's

In [76]:
def my_auxiliary_match(prediction, expected):
    '''
        Check if auxiliary matches for generalization set.

        Args:
            prediciton: list of words
            expected: list of words
        Return:
            boolean
    '''
    if prediction[0] == expected[0]:
        return True

    return False
lines = open(input_file_path+'generalisation.txt' ,).\
        read().strip().split('\n')
failed_gen_pos_p = []
failed_gen_full_p = []
failed_gen_pos_e = []
failed_gen_full_e = []
total_lines_gen = 0
full_correct_gen = 0
full_correct_pos = 0
correct_aux = 0
failed_aux_p = []
failed_aux_e  = []
input_sentences=[]
output_sentences = []
predicted_sentences = []
from eval import *
for index in range(len(lines)):
    sentences = lines[index].split("\t")
    normalizedString = (sentences[0].lower()).split(" ")
    #     print(normalizedString)
    normalizedString = list(ch for ch in normalizedString if ch not in exclude)
    #     print(normalizedString)
    input_sent =" ".join(normalizedString)
    #     print(input_sent)
    normalizedString = (sentences[1].lower()).split(" ")
    #     print(normalizedString)
    normalizedString = list(ch for ch in normalizedString if ch not in exclude)
    #     print(normalizedString)
    output_sent =" ".join(normalizedString)
    input_sentences.append(input_sent)
    output_sentences.append(output_sent)
    outwords , out_attn = evaluate(encoder1,attn_decoder1,input_sent,MAX_LENGTH)
    predicted_sentence = " ".join(outwords)
    predicted_sentences.append(predicted_sentence)
    pred = list(ch for ch in outwords if ch not in exclude)
#     print(pred)
    if(pred[-1] != "." and pred[-1] != "?"):
        final_pred = pred[:len(pred)-1]
    else:
        final_expected = pred[:len(pred)-1]
    expected = output_sent.split(" ")
    final_expected = expected[:len(expected)-1]
#     print(expected)
#     print("Final expected " , final_expected)
    print("index" , total_lines_gen)
    print("Count : pos" , full_correct_pos )
    print ("Count : full" , full_correct_gen)
    print("Count : COrrect aux"  ,correct_aux)
    print("Final :" ,  final_pred,final_expected)
    if full_sentence_word_match(final_pred,final_expected):
        full_correct_gen+=1
    else:
        failed_gen_full_p.append(final_pred)
        failed_gen_full_e.append(final_expected)
    if full_sentence_pos_match(final_pred,final_expected,agreement):
        full_correct_pos+=1
    else:
        failed_gen_pos_p.append(final_pred)
        failed_gen_pos_e.append(final_expected)
    if my_auxiliary_match(final_pred , final_expected):
        correct_aux+=1
    else:
        failed_aux_p.append(final_pred)
        failed_aux_e.append(final_expected)

    total_lines_gen+=1

predictions = open(input_file_path+"predictions_gen_" + str(counter-1) + ".txt","w")
for index in range(total_lines_gen):
    predictions.write(str(index)+".\n")
    predictions.write("Input:"+input_sentences[index] + "\n")
    predictions.write("Expected Output:" + output_sentences[index]+"\n")
    predictions.write("Predicted:" + predicted_sentences[index] + "\n")
predictions.close()

report = open(input_file_path+"report_gen_" + str(counter-1) + ".txt" , "w")
report.write("Total number Of sentences:" + str(total_lines_gen) + "\n")
report.write("Total number of correct full sentences word match:" + str(full_correct_gen) + "\n")
report.write("Total number of correct full sentences pos match:" + str(full_correct_pos) + "\n")
report.write("Total number of correct auxillary locations:" + str(correct_aux) + "\n")
report.close()

failed = open(input_file_path+"failed_full_gen_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_gen_full_p)):
    predicted = " ".join(failed_gen_full_p[index])
    expected = " ".join(failed_gen_full_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()
failed = open(input_file_path+"failed_pos_gen_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_gen_pos_p)):
    predicted = " ".join(failed_gen_pos_p[index])
    expected = " ".join(failed_gen_pos_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()
failed = open(input_file_path+"failed_aux_gen_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_aux_p)):
    predicted = " ".join(failed_aux_p[index])
    expected = " ".join(failed_aux_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()





index 0
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['will', 'your', 'monkeys', 'who', 'my', 'yak', 'could', 'admire', 'your', 'bird'] ['could', 'your', 'monkeys', 'who', 'my', 'yak', 'will', 'sleep', 'admire', 'your', 'bird']
index 1
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['can', 'some', 'monkey', 'who', 'some', 'monkey', 'would', 'live'] ['would', 'some', 'monkey', 'who', 'some', 'monkey', 'can', 'live', 'impress', 'some', 'unicorns']
index 2
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['will', 'our', 'seal', 'that', 'some', 'unicorns', 'can', 'smile', 'can', 'smile'] ['can', 'our', 'seal', 'that', 'some', 'unicorns', 'will', 'smile', 'smile']
index 3
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['can', 'our', 'elephants', 'who', 'will', 'smile', 'will', 'irritate', 'my', 'dogs', 'who', 'can', 'irritate', 'my', 'dogs'] ['will', 'our', 'elephants', 'who', 'can', 'smile', 'irritate', 'my', 'dogs', 'who', 'can', 'irritate',

index 37
Count : pos 1
Count : full 0
Count : COrrect aux 0
Final : ['would', 'her', 'yak', 'who', 'can', 'live', 'can', 'admire', 'my', 'yak', 'that', 'would', 'admire', 'my', 'yak'] ['can', 'her', 'yak', 'who', 'would', 'live', 'admire', 'my', 'yak', 'that', 'would', 'admire', 'my', 'yak']
index 38
Count : pos 1
Count : full 0
Count : COrrect aux 0
Final : ['will', 'your', 'yaks', 'who', 'your', 'yaks', 'will', 'impress', 'your', 'yaks', 'who', 'our', 'elephants', 'will', 'live'] ['could', 'your', 'yaks', 'who', 'will', 'read', 'impress', 'your', 'yaks', 'who', 'our', 'elephants', 'will', 'live']
index 39
Count : pos 1
Count : full 0
Count : COrrect aux 0
Final : ['would', 'our', 'dogs', 'who', 'our', 'rabbit', 'who', 'confuse', 'your', 'rabbit', 'who', 'would', 'giggle'] ['can', 'our', 'dogs', 'who', 'would', 'giggle', 'confuse', 'your', 'rabbit', 'who', 'your', 'rabbit', 'would', 'read']
index 40
Count : pos 1
Count : full 0
Count : COrrect aux 0
Final : ['would', 'my', 'birds', 'w

index 75
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['could', 'my', 'seals', 'that', 'some', 'elephants', 'read', 'would', 'confuse', 'some', 'seals'] ['would', 'my', 'seals', 'that', 'some', 'elephants', 'could', 'read', 'confuse', 'some', 'seals']
index 76
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['will', 'her', 'monkey', 'who', 'her', 'monkey', 'can', 'laugh'] ['can', 'her', 'monkey', 'who', 'her', 'monkey', 'will', 'laugh', 'live']
index 77
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['would', 'the', 'dogs', 'that', 'some', 'rabbits', 'could', 'laugh'] ['could', 'the', 'dogs', 'that', 'some', 'rabbits', 'would', 'laugh', 'laugh']
index 78
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['can', 'some', 'yaks', 'who', 'some', 'rabbits', 'would', 'giggle'] ['would', 'some', 'yaks', 'who', 'some', 'rabbits', 'can', 'giggle', 'impress', 'her', 'rabbits']
index 79
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['coul

index 114
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['could', 'her', 'dogs', 'that', 'some', 'dogs', 'would', 'read', 'impress', 'some', 'dogs', 'that', 'would', 'impress', 'some', 'dogs'] ['would', 'her', 'dogs', 'that', 'could', 'read', 'impress', 'some', 'dogs', 'around', 'some', 'dogs']
index 115
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['will', 'our', 'yak', 'that', 'some', 'unicorns', 'can', 'giggle', 'some', 'impress', 'some', 'seals'] ['can', 'our', 'yak', 'that', 'will', 'giggle', 'impress', 'some', 'unicorns', 'by', 'some', 'seals']
index 116
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['would', 'some', 'elephant', 'who', 'some', 'seal', 'giggle', 'can', 'confuse', 'some', 'seal'] ['can', 'some', 'elephant', 'who', 'some', 'seal', 'would', 'giggle', 'confuse', 'some', 'seal']
index 117
Count : pos 1
Count : full 0
Count : COrrect aux 1
Final : ['would', 'her', 'yaks', 'who', 'the', 'elephants', 'could', 'call', 'the', 'elephan

index 150
Count : pos 3
Count : full 0
Count : COrrect aux 1
Final : ['would', 'some', 'cats', 'who', 'some', 'cats', 'would', 'irritate', 'the', 'unicorn', 'that', 'some', 'cats', 'would', 'giggle'] ['can', 'some', 'cats', 'who', 'would', 'giggle', 'irritate', 'the', 'unicorn', 'that', 'some', 'cats', 'would', 'giggle']
index 151
Count : pos 3
Count : full 0
Count : COrrect aux 1
Final : ['would', 'our', 'bird', 'that', 'our', 'cats', 'could', 'laugh'] ['could', 'our', 'bird', 'that', 'would', 'entertain', 'our', 'cats', 'laugh']
index 152
Count : pos 3
Count : full 0
Count : COrrect aux 1
Final : ['could', 'the', 'cat', 'who', 'will', 'admire', 'the', 'yaks', 'sleep'] ['will', 'the', 'cat', 'who', 'could', 'admire', 'the', 'yaks', 'sleep']
index 153
Count : pos 4
Count : full 0
Count : COrrect aux 1
Final : ['will', 'some', 'yaks', 'who', 'some', 'seals', 'could', 'live', 'the', 'yaks'] ['could', 'some', 'yaks', 'who', 'some', 'seals', 'will', 'live', 'entertain', 'the', 'yaks']
inde

...

Count : COrrect aux 156
Final : ['would', 'our', 'elephant', 'who', 'my', 'elephant', 'can', 'laugh', 'can', 'laugh'] ['can', 'our', 'elephant', 'who', 'would', 'call', 'my', 'elephant', 'laugh']
index 9847
Count : pos 184
Count : full 8
Count : COrrect aux 156
Final : ['can', 'her', 'dog', 'that', 'her', 'cats', 'sleep', 'would', 'smile'] ['would', 'her', 'dog', 'that', 'her', 'cats', 'can', 'sleep', 'smile']
index 9848
Count : pos 184
Count : full 8
Count : COrrect aux 156
Final : ['could', 'the', 'unicorns', 'who', 'can', 'smile', 'can', 'irritate', 'your', 'yaks'] ['can', 'the', 'unicorns', 'who', 'could', 'smile', 'irritate', 'your', 'yaks']
index 9849
Count : pos 184
Count : full 8
Count : COrrect aux 156
Final : ['would', 'some', 'cat', 'who', 'will', 'admire', 'her', 'monkeys', 'who', 'would', 'sleep'] ['will', 'some', 'cat', 'who', 'would', 'sleep', 'admire', 'her', 'monkeys', 'who', 'would', 'sleep']
index 9850
Count : pos 184
Count : full 8
Count : COrrect aux 156
Final : ['

index 9877
Count : pos 185
Count : full 8
Count : COrrect aux 157
Final : ['would', 'my', 'dogs', 'who', 'my', 'dogs', 'can', 'live'] ['can', 'my', 'dogs', 'who', 'would', 'impress', 'my', 'dogs', 'live']
index 9878
Count : pos 185
Count : full 8
Count : COrrect aux 157
Final : ['can', 'our', 'dogs', 'who', 'our', 'elephants', 'sleep'] ['would', 'our', 'dogs', 'who', 'our', 'elephants', 'can', 'sleep', 'impress', 'some', 'dogs']
index 9879
Count : pos 185
Count : full 8
Count : COrrect aux 157
Final : ['would', 'our', 'rabbits', 'who', 'my', 'elephant', 'will', 'giggle', 'my', 'dog'] ['will', 'our', 'rabbits', 'who', 'my', 'elephant', 'would', 'giggle', 'entertain', 'my', 'dog']
index 9880
Count : pos 185
Count : full 8
Count : COrrect aux 157
Final : ['can', 'your', 'cats', 'who', 'your', 'giggle', 'will', 'irritate', 'your', 'unicorn', 'who', 'can', 'irritate', 'her', 'unicorn'] ['will', 'your', 'cats', 'that', 'can', 'giggle', 'irritate', 'your', 'unicorn', 'who', 'can', 'irritate',

index 9917
Count : pos 187
Count : full 8
Count : COrrect aux 157
Final : ['can', 'our', 'cat', 'who', 'our', 'yaks', 'will', 'impress', 'our', 'cat', 'near', 'our', 'cat'] ['will', 'our', 'cat', 'who', 'can', 'laugh', 'impress', 'our', 'yaks', 'near', 'our', 'cat']
index 9918
Count : pos 187
Count : full 8
Count : COrrect aux 157
Final : ['will', 'your', 'unicorns', 'that', 'my', 'seals', 'would', 'live'] ['would', 'your', 'unicorns', 'that', 'will', 'confuse', 'my', 'seals', 'live']
index 9919
Count : pos 187
Count : full 8
Count : COrrect aux 157
Final : ['can', 'the', 'monkey', 'who', 'the', 'monkey', 'will', 'smile'] ['would', 'the', 'monkey', 'who', 'the', 'monkey', 'can', 'smile', 'live']
index 9920
Count : pos 187
Count : full 8
Count : COrrect aux 157
Final : ['can', 'my', 'cat', 'who', 'some', 'seal', 'would', 'irritate', 'some', 'seal', 'by', 'some', 'seal'] ['would', 'my', 'cat', 'who', 'can', 'live', 'irritate', 'some', 'seal', 'by', 'some', 'seal']
index 9921
Count : pos 

index 9955
Count : pos 187
Count : full 8
Count : COrrect aux 157
Final : ['can', 'the', 'cats', 'who', 'could', 'entertain', 'the', 'cats', 'could', 'laugh'] ['could', 'the', 'cats', 'who', 'can', 'entertain', 'the', 'cats', 'laugh']
index 9956
Count : pos 187
Count : full 8
Count : COrrect aux 157
Final : ['would', 'our', 'dog', 'who', 'will', 'smile', 'will', 'call', 'my', 'dogs', 'that', 'my', 'dogs', 'would', 'smile'] ['will', 'our', 'dog', 'who', 'would', 'smile', 'call', 'my', 'dogs', 'that', 'my', 'dogs', 'would', 'smile']
index 9957
Count : pos 187
Count : full 8
Count : COrrect aux 157
Final : ['could', 'her', 'yaks', 'who', 'call', 'the', 'elephants'] ['would', 'her', 'yaks', 'who', 'could', 'smile', 'call', 'the', 'elephants']
index 9958
Count : pos 187
Count : full 8
Count : COrrect aux 157
Final : ['can', 'your', 'rabbits', 'who', 'could', 'laugh', 'could', 'entertain', 'your', 'unicorns', 'near', 'your', 'cat'] ['could', 'your', 'rabbits', 'who', 'can', 'laugh', 'enterta

index 9994
Count : pos 189
Count : full 8
Count : COrrect aux 157
Final : ['will', 'my', 'monkeys', 'that', 'my', 'monkeys', 'could', 'impress', 'my', 'monkeys', 'near', 'her', 'monkeys'] ['could', 'my', 'monkeys', 'that', 'will', 'giggle', 'impress', 'my', 'monkeys', 'near', 'her', 'monkeys']
index 9995
Count : pos 189
Count : full 8
Count : COrrect aux 157
Final : ['would', 'your', 'cat', 'who', 'the', 'dog', 'can', 'entertain', 'your', 'dog'] ['can', 'your', 'cat', 'who', 'would', 'laugh', 'entertain', 'your', 'dog', 'by', 'the', 'cat']
